In [1]:
import logging

import gym
import numpy as np
import pandas as pd
import random
from docopt import docopt
from enum import Enum


from gym import Env
from gym.spaces import Discrete
from gym_env.env import PlayerShell

from tools.helper import get_config
from tools.helper import init_logger
from tools.hand_evaluator import get_winner
from tools.helper import flatten

import logging
import time

import numpy as np

from gym_env.env import Action
from gym_env.rendering import PygletWindow, WHITE, RED, GREEN, BLUE, GRAY

import tensorflow as tf
import json

from tensorflow.keras.models import Sequential, model_from_json
from tensorflow.keras.callbacks import TensorBoard
from tensorflow.keras.layers import Dense, Dropout
from tensorflow.keras.optimizers import Adam

from rl.policy import BoltzmannQPolicy
from rl.memory import SequentialMemory
from rl.agents import DQNAgent
from rl.core import Processor

In [2]:
class CommunityData:
    """Data available to everybody"""

    def __init__(self, num_players):
        """data"""
        self.current_player_position = [False] * num_players  # ix[0] = dealer
        self.stage = [False] * 4  # one hot: preflop, flop, turn, river
        self.community_pot = None
        self.current_round_pot = None
        self.active_players = [False] * num_players  # one hot encoded, 0 = dealer
        self.big_blind = 0
        self.small_blind = 0
        self.legal_moves = [0 for action in Action]

In [3]:
class StageData:
    """Pre-flop, flop, turn, river, and showdown"""
    def __init__(self, num_players):
        """data"""
        self.calls = [False] * num_players  # ix[0] = dealer
        self.raises = [False] * num_players  # ix[0] = dealer
        self.min_call_at_action = [0] * num_players  # ix[0] = dealer
        self.contribution = [0] * num_players  # ix[0] = dealer
        self.stack_at_action = [0] * num_players  # ix[0] = dealer
        self.community_pot_at_action = [0] * num_players  # ix[0] = dealer



In [4]:
class PlayerData:
    """Player specific information"""
    def __init__(self):
        self.position = None
        self.equity_to_river_alive = 0
        self.equity_to_river_2plr = 0
        self.equity_to_river_3plr = 0
        self.stack = None

In [5]:
class Stage(Enum):
    """Defining the stages of the game"""
    PREFLOP = 0
    FLOP = 1
    TURN = 2
    RIVER = 3
    END_HIDDEN = 4
    SHOWDOWN = 5

In [6]:
class Action(Enum):
    """Allowed actions"""
    FOLD = 0
    CHECK = 1
    CALL = 2
    RAISE_3BB = 3
    RAISE_HALF_POT = 3
    RAISE_POT = 4
    RAISE_2POT = 5
    ALL_IN = 6
    SMALL_BLIND = 7
    BIG_BLIND = 8

In [7]:
class HoldemTable(Env):
    """Game environment"""

    def __init__(self, initial_stacks=100, small_blind=1, big_blind=2, render=False, funds_plot=True,
                 max_raising_rounds=2, use_cpp_montecarlo=False):
        if use_cpp_montecarlo:
            import cppimport
            calculator = cppimport.imp("tools.montecarlo_cpp.pymontecarlo")
            get_equity = calculator.montecarlo
        else:
            from tools.montecarlo_python import get_equity
        self.get_equity = get_equity
        self.use_cpp_montecarlo = use_cpp_montecarlo
        self.num_of_players = 0
        self.small_blind = small_blind
        self.big_blind = big_blind
        self.render_switch = render
        self.players = []
        self.table_cards = None
        self.dealer_pos = None
        self.player_status = []  # one hot encoded
        self.current_player = None
        self.player_cycle = None  # cycle iterator
        self.stage = None
        self.last_player_pot = None
        self.viewer = None
        self.player_max_win = None  # used for side pots
        self.second_round = False
        self.last_caller = None
        self.last_raiser = None
        self.raisers = []
        self.callers = []
        self.played_in_round = None
        self.min_call = None
        self.community_data = None
        self.player_data = None
        self.stage_data = None
        self.deck = None
        self.action = None
        self.winner_ix = None
        self.initial_stacks = initial_stacks
        self.acting_agent = None
        self.funds_plot = funds_plot
        self.max_round_raising = max_raising_rounds

        # pots
        self.community_pot = 0
        self.current_round_pot = 9
        self.player_pots = None  # individual player pots

        self.observation = None
        self.reward = None
        self.info = None
        self.done = False
        self.funds_history = None
        self.array_everything = None
        self.legal_moves = None
        self.illegal_move_reward = -1
        self.action_space = Discrete(len(Action) - 2)
        self.first_action_for_hand = None

    def reset(self):
        """Reset after game over."""
        self.observation = None
        self.reward = None
        self.info = None
        self.done = False
        self.funds_history = pd.DataFrame()
        self.first_action_for_hand = [True] * len(self.players)

        for player in self.players:
            player.stack = self.initial_stacks

        self.dealer_pos = 0
        self.player_cycle = PlayerCycle(self.players, dealer_idx=-1, max_steps_after_raiser=len(self.players) - 1,
                                        max_steps_after_big_blind=len(self.players))
        self._start_new_hand()
        self._get_environment()
        # auto play for agents where autoplay is set
        if self._agent_is_autoplay() and not self.done:
            self.step('initial_player_autoplay')  # kick off the first action after bb by an autoplay agent

        return self.array_everything

    def step(self, action):  # pylint: disable=arguments-differ
        self.reward = 0
        self.acting_agent = self.player_cycle.idx
        if self._agent_is_autoplay():
            while self._agent_is_autoplay() and not self.done:
                log.debug("Autoplay agent. Call action method of agent.")
                self._get_environment()
                # call agent's action method
                action = self.current_player.agent_obj.action(self.legal_moves, self.observation, self.info)
                if Action(action) not in self.legal_moves:
                    self._illegal_move(action)
                else:
                    self._execute_step(Action(action))
                    if self.first_action_for_hand[self.acting_agent] or self.done:
                        self.first_action_for_hand[self.acting_agent] = False
                        self._calculate_reward(action)

        else:  # action received from player shell (e.g. keras rl, not autoplay)
            self._get_environment()  # get legal moves
            if Action(action) not in self.legal_moves:
                self._illegal_move(action)
            else:
                self._execute_step(Action(action))
                if self.first_action_for_hand[self.acting_agent] or self.done:
                    self.first_action_for_hand[self.acting_agent] = False
                    self._calculate_reward(action)

            log.info(f"Previous action reward for seat {self.acting_agent}: {self.reward}")
        return self.array_everything, self.reward, self.done, self.info

    def _execute_step(self, action):
        self._process_decision(action)

        self._next_player()

        if self.stage in [Stage.END_HIDDEN, Stage.SHOWDOWN]:
            self._end_hand()
            self._start_new_hand()

        self._get_environment()

    def _illegal_move(self, action):
        log.warning(f"{action} is an Illegal move, try again. Currently allowed: {self.legal_moves}")
        self.reward = self.illegal_move_reward

    def _agent_is_autoplay(self, idx=None):
        if not idx:
            return hasattr(self.current_player.agent_obj, 'autoplay')
        return hasattr(self.players[idx].agent_obj, 'autoplay')

    def _get_environment(self):
        """Observe the environment"""
        if not self.done:
            self._get_legal_moves()

        self.observation = None
        self.reward = 0
        self.info = None

        self.community_data = CommunityData(len(self.players))
        self.community_data.community_pot = self.community_pot / (self.big_blind * 100)
        self.community_data.current_round_pot = self.current_round_pot / (self.big_blind * 100)
        self.community_data.small_blind = self.small_blind
        self.community_data.big_blind = self.big_blind
        self.community_data.stage[np.minimum(self.stage.value, 3)] = 1
        self.community_data.legal_moves = [action in self.legal_moves for action in Action]

        self.player_data = PlayerData()
        self.player_data.stack = [player.stack / (self.big_blind * 100) for player in self.players]

        if not self.current_player:  # game over
            self.current_player = self.players[self.winner_ix]

        self.player_data.position = self.current_player.seat
        self.current_player.equity_alive = self.get_equity(set(self.current_player.cards), set(self.table_cards),
                                                           sum(self.player_cycle.alive), 1000)
        self.player_data.equity_to_river_alive = self.current_player.equity_alive

        arr1 = np.array(list(flatten(self.player_data.__dict__.values())))
        arr2 = np.array(list(flatten(self.community_data.__dict__.values())))
        arr3 = np.array([list(flatten(sd.__dict__.values())) for sd in self.stage_data]).flatten()

        self.array_everything = np.concatenate([arr1, arr2, arr3]).flatten()

        self.observation = self.array_everything
        self._get_legal_moves()

        self.info = {'player_data': self.player_data.__dict__,
                     'community_data': self.community_data.__dict__,
                     'stage_data': [stage.__dict__ for stage in self.stage_data],
                     'legal_moves': self.legal_moves}

        self.observation_space = self.array_everything.shape

        if self.render_switch:
            self.render()

    def _calculate_reward(self, last_action):
        _ = last_action
        if self.done:
            won = 1 if not self._agent_is_autoplay(idx=self.winner_ix) else -1
            self.reward = self.initial_stacks * len(self.players) * won
            log.debug(f"Keras-rl agent has reward {self.reward}")

        elif len(self.funds_history) > 1:
            self.reward = self.funds_history.iloc[-1, self.acting_agent] - self.funds_history.iloc[
                -2, self.acting_agent]

        else:
            pass

    def _process_decision(self, action):  # pylint: disable=too-many-statements
        """Process the decisions that have been made by an agent."""
        if action not in [Action.SMALL_BLIND, Action.BIG_BLIND]:
            assert action in set(self.legal_moves), "Illegal decision"

        if action == Action.FOLD:
            self.player_cycle.deactivate_current()
            self.player_cycle.mark_folder()

        else:

            if action == Action.CALL:
                contribution = min(self.min_call - self.player_pots[self.current_player.seat],
                                   self.current_player.stack)
                self.callers.append(self.current_player.seat)
                self.last_caller = self.current_player.seat

            # verify the player has enough in his stack
            elif action == Action.CHECK:
                contribution = 0
                self.player_cycle.mark_checker()

            elif action == Action.RAISE_3BB:
                contribution = 3 * self.big_blind - self.player_pots[self.current_player.seat]
                self.raisers.append(self.current_player.seat)

            elif action == Action.RAISE_HALF_POT:
                contribution = (self.community_pot + self.current_round_pot) / 2
                self.raisers.append(self.current_player.seat)

            elif action == Action.RAISE_POT:
                contribution = (self.community_pot + self.current_round_pot)
                self.raisers.append(self.current_player.seat)

            elif action == Action.RAISE_2POT:
                contribution = (self.community_pot + self.current_round_pot) * 2
                self.raisers.append(self.current_player.seat)

            elif action == Action.ALL_IN:
                contribution = self.current_player.stack
                self.raisers.append(self.current_player.seat)

            elif action == Action.SMALL_BLIND:
                contribution = np.minimum(self.small_blind, self.current_player.stack)

            elif action == Action.BIG_BLIND:
                contribution = np.minimum(self.big_blind, self.current_player.stack)
                self.player_cycle.mark_bb()
            else:
                raise RuntimeError("Illegal action.")

            if contribution > self.min_call:
                self.player_cycle.mark_raiser()

            self.current_player.stack -= contribution
            self.player_pots[self.current_player.seat] += contribution
            self.current_round_pot += contribution
            self.last_player_pot = self.player_pots[self.current_player.seat]

            if self.current_player.stack == 0 and contribution > 0:
                self.player_cycle.mark_out_of_cash_but_contributed()

            self.min_call = max(self.min_call, contribution)

            self.current_player.actions.append(action)
            self.current_player.last_action_in_stage = action.name
            self.current_player.temp_stack.append(self.current_player.stack)

            self.player_max_win[self.current_player.seat] += contribution  # side pot

            pos = self.player_cycle.idx
            rnd = self.stage.value + self.second_round
            self.stage_data[rnd].calls[pos] = action == Action.CALL
            self.stage_data[rnd].raises[pos] = action in [Action.RAISE_2POT, Action.RAISE_HALF_POT, Action.RAISE_POT]
            self.stage_data[rnd].min_call_at_action[pos] = self.min_call / (self.big_blind * 100)
            self.stage_data[rnd].community_pot_at_action[pos] = self.community_pot / (self.big_blind * 100)
            self.stage_data[rnd].contribution[pos] += contribution / (self.big_blind * 100)
            self.stage_data[rnd].stack_at_action[pos] = self.current_player.stack / (self.big_blind * 100)

        self.player_cycle.update_alive()

        log.info(
            f"Seat {self.current_player.seat} ({self.current_player.name}): {action} - Remaining stack: {self.current_player.stack}, "
            f"Round pot: {self.current_round_pot}, Community pot: {self.community_pot}, "
            f"player pot: {self.player_pots[self.current_player.seat]}")

    def _start_new_hand(self):
        """Deal new cards to players and reset table states."""
        self._save_funds_history()

        if self._check_game_over():
            return
        log.info("")
        log.info("-------------------")
        log.info("Starting new hand.")
        log.info("-------------------")
        self.table_cards = []
        self._create_card_deck()
        self.stage = Stage.PREFLOP

        # Pre-flop, Flop, Turn, River, Showdown
        self.stage_data = [StageData(len(self.players)) for _ in range(8)]

        # Pots
        self.community_pot = 0
        self.current_round_pot = 0
        self.player_pots = [0] * len(self.players)
        self.player_max_win = [0] * len(self.players)
        self.last_player_pot = 0
        self.played_in_round = 0
        self.first_action_for_hand = [True] * len(self.players)

        for player in self.players:
            player.cards = []

        self._next_dealer()

        self._distribute_cards()
        self._initiate_round()

    def _save_funds_history(self):
        """Keep track of player funds history"""
        funds_dict = {i: player.stack for i, player in enumerate(self.players)}
        self.funds_history = pd.concat([self.funds_history, pd.DataFrame(funds_dict, index=[0])])

    def _check_game_over(self):
        """Check if only one player has money left"""
        player_alive = []
        self.player_cycle.new_hand_reset()

        for idx, player in enumerate(self.players):
            if player.stack > 0:
                player_alive.append(True)
            else:
                self.player_status.append(False)
                self.player_cycle.deactivate_player(idx)

        remaining_players = sum(player_alive)
        if remaining_players < 2:
            self._game_over()
            return True
        return False

    def _game_over(self):
        """End of an episode."""
        log.info("Game over.")
        self.done = True
        player_names = [f"{i} - {player.name}" for i, player in enumerate(self.players)]
        self.funds_history.columns = player_names
        if self.funds_plot:
            self.funds_history.reset_index(drop=True).plot()
        log.info(self.funds_history)
        plt.show()

        winner_in_episodes.append(self.winner_ix)
        league_table = pd.Series(winner_in_episodes).value_counts()
        best_player = league_table.index[0]
        log.info(league_table)
        log.info(f"Best Player: {best_player}")

    def _initiate_round(self):
        """A new round (flop, turn, river) is initiated"""
        self.last_caller = None
        self.last_raiser = None
        self.raisers = []
        self.callers = []
        self.min_call = 0
        for player in self.players:
            player.last_action_in_stage = ''
        self.player_cycle.new_round_reset()

        if self.stage == Stage.PREFLOP:
            log.info("")
            log.info("===Round: Stage: PREFLOP")
            # max steps total will be adjusted again at bb
            self.player_cycle.max_steps_total = len(self.players) * self.max_round_raising + 2

            self._next_player()
            self._process_decision(Action.SMALL_BLIND)
            self._next_player()
            self._process_decision(Action.BIG_BLIND)
            self._next_player()

        elif self.stage in [Stage.FLOP, Stage.TURN, Stage.RIVER]:
            self.player_cycle.max_steps_total = len(self.players) * self.max_round_raising

            self._next_player()

        elif self.stage == Stage.SHOWDOWN:
            log.info("Showdown")

        else:
            raise RuntimeError()

    def add_player(self, agent):
        self.num_of_players += 1
        player = PlayerShell(stack_size=self.initial_stacks, name=agent.name)
        player.agent_obj = agent
        player.seat = len(self.players)  # assign next seat number to player
        player.stack = self.initial_stacks
        self.players.append(player)
        self.player_status = [True] * len(self.players)
        self.player_pots = [0] * len(self.players)

    def _end_round(self):
        """End of preflop, flop, turn or river"""
        self._close_round()
        if self.stage == Stage.PREFLOP:
            self.stage = Stage.FLOP
            self._distribute_cards_to_table(3)

        elif self.stage == Stage.FLOP:
            self.stage = Stage.TURN
            self._distribute_cards_to_table(1)

        elif self.stage == Stage.TURN:
            self.stage = Stage.RIVER
            self._distribute_cards_to_table(1)

        elif self.stage == Stage.RIVER:
            self.stage = Stage.SHOWDOWN

        log.info("--------------------------------")
        log.info(f"===ROUND: {self.stage} ===")
        self._clean_up_pots()

    def _clean_up_pots(self):
        self.community_pot += self.current_round_pot
        self.current_round_pot = 0
        self.player_pots = [0] * len(self.players)

    def _end_hand(self):
        self._clean_up_pots()
        self.winner_ix = self._get_winner()
        self._award_winner(self.winner_ix)

    def _get_winner(self):
        """Determine which player has won the hand"""
        potential_winners = self.player_cycle.get_potential_winners()

        potential_winner_idx = [i for i, potential_winner in enumerate(potential_winners) if potential_winner]
        if sum(potential_winners) == 1:
            winner_ix = [i for i, active in enumerate(potential_winners) if active][0]
            winning_card_type = 'Only remaining player in round'

        else:
            assert self.stage == Stage.SHOWDOWN
            remaining_player_winner_ix, winning_card_type = get_winner([player.cards
                                                                        for ix, player in enumerate(self.players) if
                                                                        potential_winners[ix]],
                                                                       self.table_cards)
            winner_ix = potential_winner_idx[remaining_player_winner_ix]
        log.info(f"Player {winner_ix} won: {winning_card_type}")
        return winner_ix

    def _award_winner(self, winner_ix):
        """Hand the pot to the winner and handle side pots"""
        max_win_per_player_for_winner = self.player_max_win[winner_ix]
        total_winnings = sum(np.minimum(max_win_per_player_for_winner, self.player_max_win))
        remains = np.maximum(0, np.array(self.player_max_win) - max_win_per_player_for_winner)  # to be returned

        self.players[winner_ix].stack += total_winnings
        self.winner_ix = winner_ix
        if total_winnings < sum(self.player_max_win):
            log.info("Returning side pots")
            for i, player in enumerate(self.players):
                player.stack += remains[i]

    def _next_dealer(self):
        self.dealer_pos = self.player_cycle.next_dealer().seat

    def _next_player(self):
        """Move to the next player"""
        self.current_player = self.player_cycle.next_player()
        if not self.current_player:
            if sum(self.player_cycle.alive) < 2:
                log.info("Only one player remaining in round")
                self.stage = Stage.END_HIDDEN
            else:
                log.info("End round - no current player returned")
                self._end_round()
                # todo: in some cases no new round should be initialized bc only one player is playing only it seems
                self._initiate_round()

        elif self.current_player == 'max_steps_total' or self.current_player == 'max_steps_after_raiser':
            log.debug(self.current_player)
            log.info("End of round ")
            self._end_round()
            return

    def _get_legal_moves(self):
        """Determine what moves are allowed in the current state"""
        self.legal_moves = []
        if self.player_pots[self.current_player.seat] == max(self.player_pots):
            self.legal_moves.append(Action.CHECK)
        else:
            self.legal_moves.append(Action.CALL)
            self.legal_moves.append(Action.FOLD)

        if self.current_player.stack >= 3 * self.big_blind - self.player_pots[self.current_player.seat]:
            self.legal_moves.append(Action.RAISE_3BB)

            if self.current_player.stack >= ((self.community_pot + self.current_round_pot) / 2) >= self.min_call:
                self.legal_moves.append(Action.RAISE_HALF_POT)

            if self.current_player.stack >= (self.community_pot + self.current_round_pot) >= self.min_call:
                self.legal_moves.append(Action.RAISE_POT)

            if self.current_player.stack >= ((self.community_pot + self.current_round_pot) * 2) >= self.min_call:
                self.legal_moves.append(Action.RAISE_2POT)

            if self.current_player.stack > 0:
                self.legal_moves.append(Action.ALL_IN)

        log.debug(f"Community+current round pot pot: {self.community_pot + self.current_round_pot}")

    def _close_round(self):
        """put player_pots into community pots"""
        self.community_pot += sum(self.player_pots)
        self.player_pots = [0] * len(self.players)
        self.played_in_round = 0

    def _create_card_deck(self):
        values = "23456789TJQKA"
        suites = "CDHS"
        self.deck = []  # contains cards in the deck
        _ = [self.deck.append(x + y) for x in values for y in suites]

    def _distribute_cards(self):
        log.info(f"Dealer is at position {self.dealer_pos}")
        for player in self.players:
            player.cards = []
            if player.stack <= 0:
                continue
            for _ in range(2):
                card = np.random.randint(0, len(self.deck))
                player.cards.append(self.deck.pop(card))
            log.info(f"Player {player.seat} got {player.cards} and ${player.stack}")

    def _distribute_cards_to_table(self, amount_of_cards):
        for _ in range(amount_of_cards):
            card = np.random.randint(0, len(self.deck))
            self.table_cards.append(self.deck.pop(card))
        log.info(f"Cards on table: {self.table_cards}")

    def render(self, mode='human'):
        """Render the current state"""
        screen_width = 600
        screen_height = 400
        table_radius = 200
        face_radius = 10

        if self.viewer is None:
            self.viewer = PygletWindow(screen_width + 50, screen_height + 50)
        self.viewer.reset()
        self.viewer.circle(screen_width / 2, screen_height / 2, table_radius, color=GREEN,
                           thickness=2)

        for i in range(len(self.players)):
            degrees = i * (360 / len(self.players))
            radian = (degrees * (np.pi / 180))
            x = (face_radius + table_radius) * np.cos(radian) + screen_width / 2
            y = (face_radius + table_radius) * np.sin(radian) + screen_height / 2
            if self.player_cycle.alive[i]:
                color = GREEN
            else:
                color = GRAY
            self.viewer.circle(x, y, face_radius, color=color, thickness=20)

            try:
                if i == self.current_player.seat:
                    self.viewer.rectangle(x - 60, y, 150, -50, (255, 0, 0, 10))
            except AttributeError:
                pass
            self.viewer.text(f"{self.players[i].name}", x - 60, y - 15,
                             font_size=10,
                             color=WHITE)
            self.viewer.text(f"Player {self.players[i].seat}: {self.players[i].cards}", x - 60, y,
                             font_size=10,
                             color=WHITE)
            equity_alive = int(round(float(self.players[i].equity_alive) * 100))

            self.viewer.text(f"${self.players[i].stack} (EQ: {equity_alive}%)", x - 60, y + 15, font_size=10,
                             color=WHITE)
            try:
                self.viewer.text(self.players[i].last_action_in_stage, x - 60, y + 30, font_size=10, color=WHITE)
            except IndexError:
                pass
            x_inner = (-face_radius + table_radius - 60) * np.cos(radian) + screen_width / 2
            y_inner = (-face_radius + table_radius - 60) * np.sin(radian) + screen_height / 2
            self.viewer.text(f"${self.player_pots[i]}", x_inner, y_inner, font_size=10, color=WHITE)
            self.viewer.text(f"{self.table_cards}", screen_width / 2 - 40, screen_height / 2, font_size=10,
                             color=WHITE)
            self.viewer.text(f"${self.community_pot}", screen_width / 2 - 15, screen_height / 2 + 30, font_size=10,
                             color=WHITE)
            self.viewer.text(f"${self.current_round_pot}", screen_width / 2 - 15, screen_height / 2 + 50,
                             font_size=10,
                             color=WHITE)

            x_button = (-face_radius + table_radius - 20) * np.cos(radian) + screen_width / 2
            y_button = (-face_radius + table_radius - 20) * np.sin(radian) + screen_height / 2
            try:
                if i == self.player_cycle.dealer_idx:
                    self.viewer.circle(x_button, y_button, 5, color=BLUE, thickness=2)
            except AttributeError:
                pass

        self.viewer.update()


In [8]:
class RandomPlayer:
    """Mandatory class with the player methods"""

    def __init__(self, name='Random'):
        """Initialization of an Player Agent"""
        self.equity_alive = 0
        self.actions = []
        self.last_action_in_stage = ''
        self.temp_stack = []
        self.name = name
        self.autoplay = True

    def action(self, action_space, observation, info):  # pylint: disable=no-self-use
        """Mandatory method that calculates the move based on the observation array and the action space."""
        _ = observation  # not using the observation for random decision
        _ = info

        this_player_action_space = {Action.FOLD, Action.CHECK, Action.CALL, Action.RAISE_POT, Action.RAISE_HALF_POT,
                                    Action.RAISE_2POT}
        possible_moves = this_player_action_space.intersection(set(action_space))
        action = random.choice(list(possible_moves))
        return action


In [9]:
class PlayerCycle:
    """Handle the circularity of the Table."""

    def __init__(self, lst, start_idx=0, dealer_idx=0, max_steps_total=None,
                 last_raiser_step=None, max_steps_after_raiser=None, max_steps_after_big_blind=None):
        """Cycle over a list"""
        self.lst = lst
        self.start_idx = start_idx
        self.size = len(lst)
        self.max_steps_total = max_steps_total
        self.last_raiser_step = last_raiser_step
        self.max_steps_after_raiser = max_steps_after_raiser
        self.max_steps_after_big_blind = max_steps_after_big_blind
        self.last_raiser = None
        self.step_counter = 0
        self.steps_for_blind_betting = 2
        self.second_round = False
        self.idx = 0
        self.dealer_idx = dealer_idx
        self.can_still_make_moves_in_this_hand = []  # if the player can still play in this round
        self.alive = [True] * len(self.lst)  # if the player can still play in the following rounds
        self.out_of_cash_but_contributed = [False] * len(self.lst)
        self.new_hand_reset()
        self.checkers = 0
        self.folder = None

    def new_hand_reset(self):
        """Reset state if a new hand is dealt"""
        self.idx = self.start_idx
        self.can_still_make_moves_in_this_hand = [True] * len(self.lst)
        self.out_of_cash_but_contributed = [False] * len(self.lst)
        self.folder = [False] * len(self.lst)
        self.step_counter = 0

    def new_round_reset(self):
        """Reset the state for the next stage: flop, turn or river"""
        self.step_counter = 0
        self.second_round = False
        self.idx = self.dealer_idx
        self.last_raiser_step = len(self.lst)
        self.checkers = 0

    def next_player(self, step=1):
        """Switch to the next player in the round."""
        if sum(np.array(self.can_still_make_moves_in_this_hand) + np.array(self.out_of_cash_but_contributed)) < 2:
            log.debug("Only one player remaining")
            return False  # only one player remains

        self.idx += step
        self.step_counter += step
        self.idx %= len(self.lst)
        if self.step_counter > len(self.lst):
            self.second_round = True
        if self.max_steps_total and (self.step_counter >= self.max_steps_total):
            log.debug("Max steps total has been reached")
            return False

        if self.last_raiser:
            raiser_reference = self.last_raiser
            if self.max_steps_after_raiser and (self.step_counter > self.max_steps_after_raiser + raiser_reference):
                log.debug("max steps after raiser has been reached")
                return False
        elif self.max_steps_after_raiser and \
                (self.step_counter > self.max_steps_after_big_blind + self.steps_for_blind_betting):
            log.debug("max steps after raiser has been reached")
            return False

        if self.checkers == sum(self.alive):
            log.debug("All players checked")
            return False

        while True:
            if self.can_still_make_moves_in_this_hand[self.idx]:
                break

            self.idx += 1
            self.step_counter += 1
            self.idx %= len(self.lst)
            if self.max_steps_total and self.step_counter >= self.max_steps_total:
                log.debug("Max steps total has been reached after jumping some folders")
                return False

        self.update_alive()
        return self.lst[self.idx]

    def next_dealer(self):
        """Move the dealer to the next player that's still in the round."""
        self.dealer_idx += 1
        self.dealer_idx %= len(self.lst)

        while True:
            if self.can_still_make_moves_in_this_hand[self.dealer_idx]:
                break

            self.dealer_idx += 1
            self.dealer_idx %= len(self.lst)

        return self.lst[self.dealer_idx]

    def set_idx(self, idx):
        """Set the index to a specific player"""
        self.idx = idx

    def deactivate_player(self, idx):
        """Deactivate a pleyr if he has folded or is out of cash."""
        assert self.can_still_make_moves_in_this_hand[idx], "Already deactivated"
        self.can_still_make_moves_in_this_hand[idx] = False

    def deactivate_current(self):
        """Deactivate the current player if he has folded or is out of cash."""
        assert self.can_still_make_moves_in_this_hand[self.idx], "Already deactivated"
        self.can_still_make_moves_in_this_hand[self.idx] = False

    def mark_folder(self):
        """Mark a player as no longer eligible to win cash from the current hand"""
        self.folder[self.idx] = True

    def mark_raiser(self):
        """Mark a raise for the current player."""
        if self.step_counter > 2:
            self.last_raiser = self.step_counter

    def mark_checker(self):
        """Counter the number of checks in the round"""
        self.checkers += 1

    def mark_out_of_cash_but_contributed(self):
        """Mark current player as a raiser or caller, but is out of cash."""
        self.out_of_cash_but_contributed[self.idx] = True
        self.deactivate_current()

    def mark_bb(self):
        """Ensure bb can raise"""
        self.last_raiser_step = self.step_counter + len(self.lst)
        self.max_steps_total = self.step_counter + len(self.lst) * 2

    def is_raising_allowed(self):
        """Check if raising is still allowed at this position"""
        return self.step_counter <= self.last_raiser_step

    def update_alive(self):
        """Update the alive property"""
        self.alive = np.array(self.can_still_make_moves_in_this_hand) + \
                     np.array(self.out_of_cash_but_contributed)

    def get_potential_winners(self):
        """Players eligible to win the pot"""
        potential_winners = np.logical_and(np.logical_or(np.array(self.can_still_make_moves_in_this_hand),
                                                         np.array(self.out_of_cash_but_contributed)),
                                           np.logical_not(np.array(self.folder)))
        return potential_winners



In [10]:
class PlayerShell:
    """Player shell"""
    def __init__(self, stack_size, name):
        """Initiaization of an agent"""
        self.stack = stack_size
        self.seat = None
        self.equity_alive = 0
        self.actions = []
        self.last_action_in_stage = ''
        self.temp_stack = []
        self.name = name
        self.agent_obj = None

In [11]:
class RandomPlayer:
    """Mandatory class with the player methods"""

    def __init__(self, name='Random'):
        """Initialization of an Player Agent"""
        self.equity_alive = 0
        self.actions = []
        self.last_action_in_stage = ''
        self.temp_stack = []
        self.name = name
        self.autoplay = True

    def action(self, action_space, observation, info):  # pylint: disable=no-self-use
        """Mandatory method that calculates the move based on the observation array and the action space."""
        _ = observation  # not using the observation for random decision
        _ = info

        this_player_action_space = {Action.FOLD, Action.CHECK, Action.CALL, Action.RAISE_POT, Action.RAISE_HALF_POT,
                                    Action.RAISE_2POT}
        possible_moves = this_player_action_space.intersection(set(action_space))
        action = random.choice(list(possible_moves))
        return action


In [12]:
class EquityPlayer:
    """Mandatory class with the player methods"""

    def __init__(self, name='Random', min_call_equity=None, min_bet_equity=None):
        """Initialization of an agent"""
        self.equity_alive = 0
        self.name = name
        self.min_call_equity = min_call_equity
        self.min_bet_equity = min_bet_equity
        self.autoplay = True

    def action(self, action_space, observation, info):  # pylint: disable=no-self-use
        """Mandatory method that calculates the move based on the observation array and the action space."""
        _ = observation
        equity_alive = info['player_data']['equity_to_river_alive']

        increment1 = .1
        increment2 = .2

        if equity_alive > self.min_bet_equity + increment2 and Action.ALL_IN in action_space:
            action = Action.ALL_IN
        elif equity_alive > self.min_bet_equity + increment1 and Action.RAISE_2POT in action_space:
            action = Action.RAISE_2POT
        elif equity_alive > self.min_bet_equity and Action.RAISE_POT in action_space:
            action = Action.RAISE_POT
        elif equity_alive > self.min_bet_equity - increment1 and Action.RAISE_HALF_POT in action_space:
            action = Action.RAISE_HALF_POT
        elif equity_alive > self.min_call_equity and Action.CALL in action_space:
            action = Action.CALL
        elif Action.CHECK in action_space:
            action = Action.CHECK
        else:
            action = Action.FOLD
        return action


In [13]:
class DQNPlayer:
    """Mandatory class with the player methods"""

    def __init__(self, name='DQN', load_model=None, env=None):
        """Initiaization of an agent"""
        self.equity_alive = 0
        self.actions = []
        self.last_action_in_stage = ''
        self.temp_stack = []
        self.name = name
        self.autoplay = True

        self.dqn = None
        self.model = None
        self.env = env

        if load_model:
            self.load(load_model)

    def initiate_agent(self, env):
        """Initialization of the DQN Agent"""
        tf.compat.v1.disable_eager_execution()

        self.env = env

        nb_actions = self.env.action_space.n

        self.model = Sequential()
        self.model.add(Dense(512, activation='relu', input_shape=env.observation_space))
        self.model.add(Dropout(0.2))
        self.model.add(Dense(512, activation='relu'))
        self.model.add(Dropout(0.2))
        self.model.add(Dense(512, activation='relu'))
        self.model.add(Dropout(0.2))
        self.model.add(Dense(nb_actions, activation='linear'))

        memory = SequentialMemory(limit=memory_limit, window_length=window_length)
        policy = TrumpPolicy()

        nb_actions = env.action_space.n

        self.dqn = DQNAgent(model=self.model, nb_actions=nb_actions, memory=memory, nb_steps_warmup=nb_steps_warmup,
                            target_model_update=1e-2, policy=policy,
                            processor=CustomProcessor(),
                            batch_size=batch_size, train_interval=train_interval, enable_double_dqn=enable_double_dqn)
        self.dqn.compile(Adam(lr=1e-3), metrics=['mae'])

    def start_step_policy(self, observation):
        """Custom policy for random decisions for warm up."""
        log.info("Random action")
        _ = observation
        action = self.env.action_space.sample()
        return action

    def train(self, env_name):
        """Train a model"""
        # initiate training loop
        timestr = time.strftime("%Y%m%d-%H%M%S") + "_" + str(env_name)
        tensorboard = TensorBoard(log_dir='./Graph/{}'.format(timestr), histogram_freq=0, write_graph=True,
                                  write_images=False)

        self.dqn.fit(self.env, nb_max_start_steps=nb_max_start_steps, nb_steps=nb_steps, visualize=False, verbose=2,
                     start_step_policy=self.start_step_policy, callbacks=[tensorboard])

        # Save the architecture
        dqn_json = self.model.to_json()
        with open("dqn_{}_json.json".format(env_name), "w") as json_file:
            json.dump(dqn_json, json_file)

        # After training is done, we save the final weights.
        self.dqn.save_weights('dqn_{}_weights.h5'.format(env_name), overwrite=True)

        # Finally, evaluate our algorithm for 5 episodes.
        self.dqn.test(self.env, nb_episodes=5, visualize=False)

    def load(self, env_name):
        """Load a model"""

        # Load the architecture
        with open('dqn_{}_json.json'.format(env_name), 'r') as architecture_json:
            dqn_json = json.load(architecture_json)

        self.model = model_from_json(dqn_json)
        self.model.load_weights('dqn_{}_weights.h5'.format(env_name))

    def play(self, nb_episodes=5, render=False):
        """Let the agent play"""
        memory = SequentialMemory(limit=memory_limit, window_length=window_length)
        policy = TrumpPolicy()

        class CustomProcessor(Processor):  # pylint: disable=redefined-outer-name
            """The agent and the environment"""

            def process_state_batch(self, batch):
                """
                Given a state batch, I want to remove the second dimension, because it's
                useless and prevents me from feeding the tensor into my CNN
                """
                return np.squeeze(batch, axis=1)

            def process_info(self, info):
                processed_info = info['player_data']
                if 'stack' in processed_info:
                    processed_info = {'x': 1}
                return processed_info

        nb_actions = self.env.action_space.n

        self.dqn = DQNAgent(model=self.model, nb_actions=nb_actions, memory=memory, nb_steps_warmup=nb_steps_warmup,
                            target_model_update=1e-2, policy=policy,
                            processor=CustomProcessor(),
                            batch_size=batch_size, train_interval=train_interval, enable_double_dqn=enable_double_dqn)
        self.dqn.compile(Adam(lr=1e-3), metrics=['mae'])  # pylint: disable=no-member

        self.dqn.test(self.env, nb_episodes=nb_episodes, visualize=render)

    def action(self, action_space, observation, info):  # pylint: disable=no-self-use
        """Mandatory method that calculates the move based on the observation array and the action space."""
        _ = observation  # not using the observation for random decision
        _ = info

        this_player_action_space = {Action.FOLD, Action.CHECK, Action.CALL, Action.RAISE_POT, Action.RAISE_HALF_POT,
                                    Action.RAISE_2POT}
        _ = this_player_action_space.intersection(set(action_space))

        action = None
        return action


class TrumpPolicy(BoltzmannQPolicy):
    """Custom policy when making decision based on neural network."""

    def select_action(self, q_values):
        """Return the selected action

        # Arguments
            q_values (np.ndarray): List of the estimations of Q for each action

        # Returns
            Selection action
        """
        assert q_values.ndim == 1
        q_values = q_values.astype('float64')
        nb_actions = q_values.shape[0]

        exp_values = np.exp(np.clip(q_values / self.tau, self.clip[0], self.clip[1]))
        probs = exp_values / np.sum(exp_values)
        action = np.random.choice(range(nb_actions), p=probs)
        log.info(f"Chosen action by keras-rl {action} - probabilities: {probs}")
        return action


class CustomProcessor(Processor):
    """The agent and the environment"""

    def __init__(self):
        """initizlie properties"""
        self.legal_moves_limit = None

    def process_state_batch(self, batch):
        """Remove second dimension to make it possible to pass it into cnn"""
        return np.squeeze(batch, axis=1)

    def process_info(self, info):
        if 'legal_moves' in info.keys():
            self.legal_moves_limit = info['legal_moves']
        else:
            self.legal_moves_limit = None
        return {'x': 1}  # on arrays allowed it seems

    def process_action(self, action):
        """Find nearest legal action"""
        if 'legal_moves_limit' in self.__dict__ and self.legal_moves_limit is not None:
            self.legal_moves_limit = [move.value for move in self.legal_moves_limit]
            if action not in self.legal_moves_limit:
                for i in range(5):
                    action += i
                    if action in self.legal_moves_limit:
                        break
                    action -= i * 2
                    if action in self.legal_moves_limit:
                        break
                    action += i

        return action


In [14]:
class SelfPlay:
    def __init__(self, render, num_episodes, use_cpp_montecarlo, funds_plot, stack=500):
        """Initialize"""
        self.winner_in_episodes = []
        self.use_cpp_montecarlo = use_cpp_montecarlo
        self.funds_plot = funds_plot
        self.render = render
        self.env = None
        self.num_episodes = num_episodes
        self.stack = stack
        self.log = logging.getLogger(__name__)

    def random_agents(self):
        """Create an environment with 6 random players"""
        env_name = 'neuron_poker-v0'
        num_of_plrs = 2
        self.env = gym.make(env_name, initial_stacks=self.stack, render=self.render)
        for _ in range(num_of_plrs):
            player = RandomPlayer()
            self.env.add_player(player)
        self.env.reset()

    def dqn_train_keras_rl(self, model_name):
        """Implementation of kreras-rl deep q learing."""
        env_name = 'neuron_poker-v0'
        env = gym.make(env_name, initial_stacks=self.stack, funds_plot=self.funds_plot, render=self.render,
                       use_cpp_montecarlo=self.use_cpp_montecarlo)

        np.random.seed(123)
        env.seed(123)
        env.add_player(EquityPlayer(name='equity/50/70', min_call_equity=.5, min_bet_equity=.7))
        env.add_player(EquityPlayer(name='equity/20/30', min_call_equity=.2, min_bet_equity=.3))
        env.add_player(RandomPlayer())
        env.add_player(RandomPlayer())
        env.add_player(RandomPlayer())
        env.add_player(PlayerShell(name='keras-rl', stack_size=self.stack))  # shell is used for callback to keras rl

        env.reset()

        dqn = DQNPlayer()
        dqn.initiate_agent(env)
        dqn.train(env_name=model_name)

    def dqn_play_keras_rl(self, model_name):
        """Create 6 players, one of them a trained DQN"""
        env_name = 'neuron_poker-v0'
        self.env = gym.make(env_name, initial_stacks=self.stack, render=self.render)
        self.env.add_player(EquityPlayer(name='equity/50/50', min_call_equity=.5, min_bet_equity=.5))
        self.env.add_player(EquityPlayer(name='equity/50/80', min_call_equity=.8, min_bet_equity=.8))
        self.env.add_player(EquityPlayer(name='equity/70/70', min_call_equity=.7, min_bet_equity=.7))
        self.env.add_player(EquityPlayer(name='equity/20/30', min_call_equity=.2, min_bet_equity=.3))
        self.env.add_player(RandomPlayer())
        self.env.add_player(PlayerShell(name='keras-rl', stack_size=self.stack))

        self.env.reset()

        dqn = DQNPlayer(load_model=model_name, env=self.env)
        dqn.play(nb_episodes=self.num_episodes, render=self.render)


In [15]:
runner = SelfPlay(render=False, 
                  num_episodes=100, 
                  use_cpp_montecarlo=True, 
                  funds_plot=False, 
                  stack = 20)

In [16]:
runner.dqn_train_keras_rl('my_model3')

Training for 100000 steps ...
Instructions for updating:
This property should not be used in TensorFlow 2.0, as updates are applied automatically.


1 is an Illegal move, try again. Currently allowed: [<Action.CALL: 2>, <Action.FOLD: 0>, <Action.RAISE_3BB: 3>, <Action.RAISE_3BB: 3>, <Action.RAISE_POT: 4>, <Action.RAISE_2POT: 5>, <Action.ALL_IN: 6>]


     7/100000: episode: 1, duration: 13.864s, episode steps:   7, steps per second:   1, episode reward: -141.000, mean reward: -20.143 [-120.000,  0.000], mean action: 2.143 [0.000, 3.000],  loss: --, mae: --, mean_q: --
    13/100000: episode: 2, duration: 25.366s, episode steps:   6, steps per second:   0, episode reward: -140.000, mean reward: -23.333 [-120.000,  0.000], mean action: 2.833 [1.000, 6.000],  loss: --, mae: --, mean_q: --
    56/100000: episode: 3, duration: 45.691s, episode steps:  43, steps per second:   1, episode reward: -173.000, mean reward: -4.023 [-120.000, 44.000], mean action: 3.372 [0.000, 6.000],  loss: --, mae: --, mean_q: --
    64/100000: episode: 4, duration: 37.107s, episode steps:   8, steps per second:   0, episode reward: -126.000, mean reward: -15.750 [-120.000,  0.000], mean action: 3.500 [0.000, 6.000],  loss: --, mae: --, mean_q: --
    66/100000: episode: 5, duration: 17.377s, episode steps:   2, steps per second:   0, episode reward: -120.000

1 is an Illegal move, try again. Currently allowed: [<Action.CALL: 2>, <Action.FOLD: 0>, <Action.RAISE_3BB: 3>, <Action.RAISE_POT: 4>, <Action.ALL_IN: 6>]


    73/100000: episode: 7, duration: 13.487s, episode steps:   5, steps per second:   0, episode reward: -121.000, mean reward: -24.200 [-120.000,  0.000], mean action: 2.800 [1.000, 6.000],  loss: --, mae: --, mean_q: --


...

6 is an Illegal move, try again. Currently allowed: [<Action.CHECK: 1>]
6 is an Illegal move, try again. Currently allowed: [<Action.CHECK: 1>]
6 is an Illegal move, try again. Currently allowed: [<Action.CHECK: 1>]
6 is an Illegal move, try again. Currently allowed: [<Action.CHECK: 1>]
6 is an Illegal move, try again. Currently allowed: [<Action.CHECK: 1>]
6 is an Illegal move, try again. Currently allowed: [<Action.CHECK: 1>]
6 is an Illegal move, try again. Currently allowed: [<Action.CHECK: 1>]
6 is an Illegal move, try again. Currently allowed: [<Action.CHECK: 1>]
6 is an Illegal move, try again. Currently allowed: [<Action.CHECK: 1>]
6 is an Illegal move, try again. Currently allowed: [<Action.CHECK: 1>]
6 is an Illegal move, try again. Currently allowed: [<Action.CHECK: 1>]
6 is an Illegal move, try again. Currently allowed: [<Action.CHECK: 1>]
6 is an Illegal move, try again. Currently allowed: [<Action.CHECK: 1>]
6 is an Illegal move, try again. Currently allowed: [<Action.CHE

6 is an Illegal move, try again. Currently allowed: [<Action.CHECK: 1>]
6 is an Illegal move, try again. Currently allowed: [<Action.CHECK: 1>]
6 is an Illegal move, try again. Currently allowed: [<Action.CHECK: 1>]
6 is an Illegal move, try again. Currently allowed: [<Action.CHECK: 1>]
6 is an Illegal move, try again. Currently allowed: [<Action.CHECK: 1>]
6 is an Illegal move, try again. Currently allowed: [<Action.CHECK: 1>]
6 is an Illegal move, try again. Currently allowed: [<Action.CHECK: 1>]
6 is an Illegal move, try again. Currently allowed: [<Action.CHECK: 1>]
6 is an Illegal move, try again. Currently allowed: [<Action.CHECK: 1>]
6 is an Illegal move, try again. Currently allowed: [<Action.CHECK: 1>]
6 is an Illegal move, try again. Currently allowed: [<Action.CHECK: 1>]
6 is an Illegal move, try again. Currently allowed: [<Action.CHECK: 1>]
6 is an Illegal move, try again. Currently allowed: [<Action.CHECK: 1>]
6 is an Illegal move, try again. Currently allowed: [<Action.CHE

6 is an Illegal move, try again. Currently allowed: [<Action.CHECK: 1>]
6 is an Illegal move, try again. Currently allowed: [<Action.CHECK: 1>]
6 is an Illegal move, try again. Currently allowed: [<Action.CHECK: 1>]
6 is an Illegal move, try again. Currently allowed: [<Action.CHECK: 1>]
6 is an Illegal move, try again. Currently allowed: [<Action.CHECK: 1>]
6 is an Illegal move, try again. Currently allowed: [<Action.CHECK: 1>]
6 is an Illegal move, try again. Currently allowed: [<Action.CHECK: 1>]
6 is an Illegal move, try again. Currently allowed: [<Action.CHECK: 1>]
6 is an Illegal move, try again. Currently allowed: [<Action.CHECK: 1>]
6 is an Illegal move, try again. Currently allowed: [<Action.CHECK: 1>]
6 is an Illegal move, try again. Currently allowed: [<Action.CHECK: 1>]
6 is an Illegal move, try again. Currently allowed: [<Action.CHECK: 1>]
6 is an Illegal move, try again. Currently allowed: [<Action.CHECK: 1>]
6 is an Illegal move, try again. Currently allowed: [<Action.CHE

6 is an Illegal move, try again. Currently allowed: [<Action.CHECK: 1>]
6 is an Illegal move, try again. Currently allowed: [<Action.CHECK: 1>]
6 is an Illegal move, try again. Currently allowed: [<Action.CHECK: 1>]
6 is an Illegal move, try again. Currently allowed: [<Action.CHECK: 1>]
6 is an Illegal move, try again. Currently allowed: [<Action.CHECK: 1>]
6 is an Illegal move, try again. Currently allowed: [<Action.CHECK: 1>]
6 is an Illegal move, try again. Currently allowed: [<Action.CHECK: 1>]
6 is an Illegal move, try again. Currently allowed: [<Action.CHECK: 1>]
6 is an Illegal move, try again. Currently allowed: [<Action.CHECK: 1>]
6 is an Illegal move, try again. Currently allowed: [<Action.CHECK: 1>]
6 is an Illegal move, try again. Currently allowed: [<Action.CHECK: 1>]
6 is an Illegal move, try again. Currently allowed: [<Action.CHECK: 1>]
6 is an Illegal move, try again. Currently allowed: [<Action.CHECK: 1>]
6 is an Illegal move, try again. Currently allowed: [<Action.CHE

KeyboardInterrupt: 